In [665]:
import agentpy as ap
import numpy as np

import matplotlib.pyplot as plt
import seaborn as sns
import IPython

In [666]:
def normalize(v):
    """ Normalize a vector to length 1. """
    norm = np.linalg.norm(v)
    if norm == 0:
        return v
    return v / norm

In [667]:
class Carro(ap.Agent):

    def definirVelocidades(self):
        if self.ruta[0] == 'B' and self.ruta[1] == 'A':
            return [[0.5,0.0],[0.0,0.5],[-0.5,0.0]]
        elif self.ruta[0] == 'B' and self.ruta[1] == 'B':
            return [[0.5,0.0],[0.5,0.0],[0.5,0.0]]
        elif self.ruta[0] == 'C' and self.ruta[1] == 'B':
            return [[0.0,0.5],[0.0,0.5],[-0.5,0.0]]
        elif self.ruta[0] == 'C' and self.ruta[1] == 'C':
            if self.direccion == 1:
                return [[0.0,0.5],[0.0,0.5],[0.0,0.5]]
            else:
                return [[0.0,-0.5],[0.0,-0.5],[0.0,-0.5]]
        elif self.ruta[0] == 'A' and self.ruta[1] == 'A':
            return [[-0.5,0.0],[-0.5,0.0],[-0.5,0.0]]

    def setup(self, calleAct, direccion, destino, rutaNum):
        self.temp = 0
        self.tiempoObj = 40
        self.rutaNum = rutaNum
        self.ruta = [calleAct,destino]
        self.direccion = direccion
        self.velocidadesRuta = self.definirVelocidades()
        self.seccion = 0
        self.velocity = normalize(self.velocidadesRuta[self.seccion])

    def setup_pos(self, space):
        self.space = space
        self.neighbors = space.neighbors
        self.pos = space.positions[self]

    def comprobarFrente(self,vecino):
        if ((self.velocidadesRuta[self.seccion][0] > 0.0 and vecino.pos[0] > self.pos[0]) or
            (self.velocidadesRuta[self.seccion][0] < 0.0 and vecino.pos[0] < self.pos[0]) or 
            (self.velocidadesRuta[self.seccion][1] > 0.0 and vecino.pos[1] > self.pos[1]) or
            (self.velocidadesRuta[self.seccion][1] < 0.0 and vecino.pos[1] < self.pos[1])):
            return True
        else:
            return False

    def evitarColision(self):
        for i in self.neighbors(self, distance = 1):
            if i.velocity[0] == 0.0 and i.velocity[1] == 0.0 and self.comprobarFrente(i):
                return True
        return False

    def revisarSemaforo(self, semaforo):
        self.temp += 1
        pos = self.pos

        luz = semaforo.mostrarLuz()

        if(self.seccion == 1 and not (pos[0] in range(semaforo.rangoInter[0][0]+2,semaforo.rangoInter[0][1]-2) and pos[1] in range(semaforo.rangoInter[1][0]+2,semaforo.rangoInter[1][1]-2))):
            self.seccion = 2

        if(self.evitarColision()):
            return normalize([0.0,0.0])

        if(self.seccion == 0):
            if(luz[1] == 1 and 
                (pos[0] in range(semaforo.rangoInter[0][0]-5,semaforo.rangoInter[0][0]) or pos[0] in range(semaforo.rangoInter[0][1],semaforo.rangoInter[0][0]+5)) or
                (pos[1] in range(semaforo.rangoInter[1][0]-5,semaforo.rangoInter[1][0]) or pos[1] in range(semaforo.rangoInter[1][1],semaforo.rangoInter[1][1]+5))):
                return normalize([self.velocidadesRuta[self.seccion][0]/2,self.velocidadesRuta[self.seccion][1]/2])
            elif((luz[1] == 2 or not np.array_equal(luz[0],self.ruta)) and (pos[0] in range(semaforo.rangoInter[0][0]-1,semaforo.rangoInter[0][1]+1) and pos[1] in range(semaforo.rangoInter[1][0]-3,semaforo.rangoInter[1][1]+3))):
                return normalize([0.0,0.0])
            elif(luz[1] == 0 and np.array_equal(luz[0],self.ruta) and (pos[0] in range(semaforo.rangoInter[0][0]+2,semaforo.rangoInter[0][1]-2) and pos[1] in range(semaforo.rangoInter[1][0]+2,semaforo.rangoInter[1][1]-2))):
                self.seccion = 1
                return normalize(self.velocidadesRuta[self.seccion])
            else:
                return normalize(self.velocidadesRuta[self.seccion])
        else:
            return normalize(self.velocidadesRuta[self.seccion])  

    def revisarDestino(self, model, semaforo):
        if 0 in self.pos or 40 in self.pos:
            
            if(self.temp > self.tiempoObj):
                semaforo.actualizarRuta(self.rutaNum)

            model.space.remove_agents(self)
            model.agents.remove(self)
            model.agentsActive.remove(self)

    def update_velocity(self, semaforo):
        self.velocity = self.revisarSemaforo(semaforo)

    def update_position(self):
        self.space.move_by(self, self.velocity)


In [668]:
class Semaforo(ap.Agent):

    def setup(self, rutas, tiempoRutas):
        self.color = 0
        self.rutaAct = 0
        self.rutas = rutas
        self.tiempoRutas = tiempoRutas
                
    
    def setupSpace(self, space):
        self.space = space
        self.pos = space.positions[self]
        self.rangoInter = [[20,30],[5,35]]

    def mostrarLuz(self):
        return [self.rutas[self.rutaAct], self.color]

    def actualizarRuta(self, numRuta):
        for i in range(0,len(self.rutas)):
            if i == numRuta:
                self.tiempoRutas[i][0] -= 1
                self.tiempoRutas[i][1] -= 1
                self.tiempoRutas[i][2] -= 1
            else:
                self.tiempoRutas[i][0] += 1
                self.tiempoRutas[i][1] += 1
                self.tiempoRutas[i][2] += 1


    def siguienteLuz(self, tiempo):
        if(tiempo >= self.tiempoRutas[self.rutaAct][self.color]):
            if(self.color == 2):
                self.color = 0
                if(self.rutaAct == len(self.rutas)-1):
                    self.rutaAct = 0
                else:
                    self.rutaAct += 1
            else:
                self.color+=1
            return True
        return False


In [669]:
class CarModel(ap.Model):
    
    def setup(self):
        self.time = 0
        self.agentNum = 0
        self.space = ap.Space(self, shape=[self.p.size]*self.p.ndim)

        rutasDisp = [['B','A'],['B','B'],['C','B'],['C','C'],['C','C'],['A','A']]
        posiciones = [(1,20),(1,23),(23,1),(27,1),(24,39),(35,30)]

        origenes = []
        destinos = []
        direcciones = []
        numerosRuta = []
        self.posicionesIniciales = []

        for i in range(1,20):
            rutaIdx = self.random.randint(0,5)
            ruta = rutasDisp[rutaIdx]
            origenes.append(ruta[0])
            destinos.append(ruta[1])
            numerosRuta.append(rutaIdx)
            if (rutaIdx == 4):
                direcciones.append(2)
            else:
                direcciones.append(1)
            self.posicionesIniciales.append(posiciones[rutaIdx])

        
        origenesPar = ap.AttrIter(origenes)
        destinosPar = ap.AttrIter(destinos)
        direccionesPar = ap.AttrIter(direcciones)
        numerosRutaPar = ap.AttrIter(numerosRuta)
                
        self.agents = ap.AgentDList(self,19,Carro,calleAct=origenesPar,direccion=direccionesPar,destino=destinosPar,rutaNum=numerosRutaPar)
        self.agentsActive = ap.AgentDList(self)
        self.agentsSem = ap.AgentDList(self,1,Semaforo,rutas=rutasDisp,tiempoRutas=[[10,10,10],[10,10,10],[10,10,10],[10,10,10],[10,10,10],[10,10,10]])

        self.space.add_agents([self.agents[0]], [self.posicionesIniciales[0]])
        self.agentsActive.append(self.agents[0])

        self.space.add_agents(self.agentsSem, [(-40,-40)])

        self.agentsActive.setup_pos(self.space)
        self.agentsSem.setupSpace(self.space)

        

    def update(self):
        if self.agentNum < 18:
            self.agentNum += 1
            self.space.add_agents([self.agents[self.agentNum]], [self.posicionesIniciales[self.agentNum]])
            self.agentsActive.append(self.agents[self.agentNum])
            self.agentsActive[self.agentNum].setup_pos(self.space)

        self.time += 1
        change = self.agentsSem[0].siguienteLuz(self.time)
        if(change):
            self.time = 0

        self.agentsActive.update_velocity(self.agentsSem[0])

        if(not self.agentsActive):
            self.stop()

    def step(self):
        self.agentsActive.update_position()
        self.agentsActive.revisarDestino(self,self.agentsSem[0])


    def mostrarSemaforo(self):
        return self.agentsSem[0].mostrarLuz()
    
    def mostrarRutas(self):
        return self.agentsSem.rutas

    def mostrarTiempoRutas(self):
        return self.agentsSem.tiempoRutas

In [670]:
def animation_plot_single(m, ax):
    ndim = m.p.ndim
    ax.set_title(f"Semáforo: {m.mostrarSemaforo()}\n"
                f"Rutas: {m.mostrarRutas()}\n"
                f"Tiempos: {m.mostrarTiempoRutas()}")
    pos = m.space.positions.values()
    pos = np.array(list(pos)).T  # Transform
    ax.scatter(*pos, s=1, c='black')
    ax.set_xlim(0, m.p.size)
    ax.set_ylim(0, m.p.size)
    if ndim == 3:
        ax.set_zlim(0, m.p.size)
    ax.set_axis_off()

def animation_plot(m, p):
    projection = '3d' if p['ndim'] == 3 else None
    fig = plt.figure(figsize=(7,7))
    ax = fig.add_subplot(111, projection=projection)
    animation = ap.animate(m(p), fig, ax, animation_plot_single)
    return IPython.display.HTML(animation.to_jshtml(fps=20))

In [671]:
parameters2D = {
    'size': 40,
    'steps': 300,
    'ndim': 2
}

In [672]:
animation_plot(CarModel, parameters2D)